# Estimate wind speeds from flight data



In [2]:
from flightanalysis import Section
import plotly.express as px
from geometry import Points
from geometry import Point


sec = Section.from_csv("examples/snap_roll_section.csv")


Difference between airspeed * body x axis and the velocity vector gives the wind vector. But, airspeed is not known. 

proposed solution - assume a wind field, direction and magnitude. Subtract the local wind speed from the body velocity vector. Resulting vector should have the same heading as the body x axis. use the direction and magnitude parameters as variables to minimize the heading error between the two vectors. 



In [3]:
import numpy as np
def wind_speed(h, v0, h0=300.0, a=0.2):
    return v0 * (h/h0)**a

def wind_vector(head, h, v0, h0=300.0, a=0.2):
    speed = wind_speed(h, v0, h0, a)
    return np.array([speed * np.cos(head), speed * np.sin(head), np.zeros(len(h))])


h = np.linspace(0, 300, 1000)
vecs = Points(wind_vector(np.radians(30), h, 20).T)
vecdf = vecs.to_pandas()
vecdf.index = h
px.line(vecdf, width=500, height=300)

In [4]:

def get_wind_error(args: np.ndarray) -> float:
    #wind vectors at the local positions
    local_wind = Points(wind_vector(args[0], np.maximum(sec.gpos.z, 0), args[1], args[2]).T)

    #wind vectors in body frame
    body_wind = sec.gatt.inverse().transform_point(local_wind)

    #body frame velocity - wind vector should be wind axis velocity
    #error in wind axis velocity, is the non x axis part (because we fly forwards)
    air_vec_error = (sec.gbvel - body_wind) * Point(0,1,1)

    #but the wind is only horizontal, so transform to world frame and remove the z component
    world_air_vec_error = sec.gatt.transform_point(air_vec_error) * Point(1,1,0)

    #the cost is the cumulative error
    return sum(abs(world_air_vec_error))

In [5]:
from scipy.optimize import minimize

res = minimize(get_wind_error, [np.pi, 5.0, 0.2], method = 'Nelder-Mead')

res

 final_simplex: (array([[3.69455327, 2.7810612 , 0.22129532],
       [3.69456356, 2.78096298, 0.22127339],
       [3.69455582, 2.78103987, 0.2212682 ],
       [3.69457004, 2.78110016, 0.22130198]]), array([23522.26587818, 23522.26588428, 23522.26590476, 23522.26591835]))
           fun: 23522.265878176655
       message: 'Optimization terminated successfully.'
          nfev: 114
           nit: 62
        status: 0
       success: True
             x: array([3.69455327, 2.7810612 , 0.22129532])

In [6]:

heads = np.linspace(0.0, 2 * np.pi, 100)
mags = np.linspace(0.0, 15.0, 10)

errs = [(mag, head, get_wind_error([head, mag, res.x[2]])) for head in heads for mag in mags]
df = pd.DataFrame(errs, columns=["windspeed", "heading", "cost"])
px.scatter(df, x="heading", y="cost", color="windspeed")

NameError: name 'pd' is not defined

In [115]:
from flightplotting.plots import plotsec
plotsec(sec.subset(275,282), nmodels=5 )

In [60]:
from flightplotting.plots import aoa_brv_plot
from flightplotting.traces import sec_col_trace
import plotly.graph_objects as go
from plotly.subplots import mQQake_subplots
import numpy as np
snap = schedule.manoeuvres[16].elements[2].get_data(aligned)
aoa_brv_plot(snap)

In [ ]:
import numpy as np
import pandas as pd

pd.DataFrame([]).reindex()